In [ ]:
-!pip install dill

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 1.9 MB/s eta 0:00:00


In [ ]:
!pip install shap

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 533.5/533.5 kB 4.1 MB/s eta 0:00:00


In [ ]:
!pip install stumpy

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 169.1/169.1 kB 3.3 MB/s eta 0:00:00


In [ ]:
!pip install pyts

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 8.5 MB/s eta 0:00:00


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import sys
sys.path.append("/content/drive/MyDrive/Nadiyah/final_codes/ts-mule_main")
sys.path.append("/content/drive/MyDrive/Nadiyah/final_codes/Window_Shap")
import dill

import numpy as np
import pandas as pd
import shap
import tensorflow as tf
tf.compat.v1.disable_v2_behavior()
import timeit
import matplotlib.pyplot as plt

from sklearn import linear_model
from sklearn.model_selection import train_test_split
from tsmule.xai.lime import LimeTS
from tsmule.sampling.segment import WindowSegmentation, MatrixProfileSegmentation, SAXSegmentation
from tsmule.sampling.perturb import Perturbation
from tsmule.xai.evaluation import PerturbationAnalysis
import windowshap

Instructions for updating:
non-resource variables are not supported in the long term


In [ ]:
rnn_model = tf.keras.models.load_model('/content/drive/MyDrive/Nadiyah/final_codes/beijing_air_multi_site_models/beijing_air_multi_site_rnn_model.h5', compile=False)

with open('/content/drive/MyDrive/Nadiyah/final_codes/beijing_air_multi_site_models/beijing_air_multi_site_test_data.dill', 'rb') as f:
    dataset_test = dill.load(f)

In [ ]:
sample=dataset_test[0]
labels=dataset_test[1]

In [ ]:
print(sample.shape)
labels.shape

(38186, 24, 11)


(38186,)

In [ ]:
def predict_fn(x):
    if len(x.shape) == 2:
        prediction = rnn_model.predict(x[np.newaxis, :, :]).ravel()
    else:
        prediction = rnn_model.predict(x).ravel()
    return prediction

#### Explanations with SHAP

In [ ]:
tic=timeit.default_timer()
shap_exp=shap.DeepExplainer(rnn_model, sample[:3000]) #expected shape (None, 24, 7)

shap_values=shap_exp.shap_values(sample)

shap_values

print('Total time: ' + str(timeit.default_timer()-tic))


KeyboardInterrupt: 

In [ ]:
shap_values=np.asarray(shap_values).squeeze()
shap_values.shape

(38186, 24, 11)

In [ ]:
with open("multi_site_dnn_shap_values.dill", 'wb') as f:
    dill.dump(shap_values, f)

### Explanation with LIME

In [ ]:
lasso_classifier = linear_model.Lasso(alpha=0.01)  #faster the model, faster LIME works
per=Perturbation() #perturbation object for LimeTS object, sampler

#### Explanation with LIME and uniform window segmentation

In [ ]:
#LimeTS object for uniform segmentation
tic = timeit.default_timer()
#segments object, WindowSegmentation object has stationery and exponential segmentations techniques
uniform_seg=WindowSegmentation(partitions=4, win_length=24)
uniform_lime=LimeTS(kernel=lasso_classifier, segmenter=uniform_seg, sampler=per, n_samples=24)
lime_values_uni=[uniform_lime.explain(sample[i], predict_fn, segmentation_method='uniform')
                 for i in range(len(sample))]
print('Total time: ' + str(timeit.default_timer()-tic))

Total time: 1646.790919434


In [ ]:
with open("/content/drive/MyDrive/Nadiyah/final_codes/shap_values/Beijing_air_quality_rnn_lime_values_uni.dill", 'wb') as f:
    dill.dump(lime_values_uni, f)

In [ ]:
lime_values_uni

Output hidden; open in https://colab.research.google.com to view.

#### Explanation with exponential window segmentation

In [ ]:
#LimeTS object for exponential window segmentation
tic = timeit.default_timer()
#segment object, WindowSegmentation has stationery and exponentials segmentation techniques
exp_seg=WindowSegmentation(partitions=4, win_length=24)
exp_lime=LimeTS(kernel=lasso_classifier, segmenter=exp_seg, sampler=per, n_samples=24)
#explainer for LimeTS
lime_values_exp=[exp_lime.explain(sample[i], predict_fn, segmentation_method='exponential')
                 for i in range(len(sample))]

print('Total time: ' + str(timeit.default_timer()-tic))

Total time: 1732.6161556099996


In [ ]:
with open("/content/drive/MyDrive/Nadiyah/final_codes/shap_values/Beijing_air_quality_rnn_lime_values_exp.dill", 'wb') as f:
    dill.dump(lime_values_exp, f)

In [ ]:
lime_values_exp

[array([[ 0.        ,  0.17736058, -0.        , -0.        ,  0.        ,
          0.1592125 , -0.08665165,  0.01675738, -0.        , -0.        ,
          0.        ],
        [ 0.        , -0.        ,  0.13683618,  0.14663778,  0.        ,
          0.        , -0.        , -0.00872402,  0.03455598,  0.        ,
         -0.04614893],
        [ 0.        , -0.        ,  0.13683618,  0.14663778,  0.        ,
          0.        , -0.        , -0.00872402,  0.03455598,  0.        ,
         -0.04614893],
        [ 0.        , -0.        ,  0.13683618,  0.14663778,  0.        ,
          0.        , -0.        , -0.00872402,  0.03455598,  0.        ,
         -0.04614893],
        [-0.        , -0.        , -0.        , -0.        ,  0.        ,
          0.14265751, -0.        ,  0.        ,  0.02593517,  0.        ,
         -0.01324696],
        [-0.        , -0.        , -0.        , -0.        ,  0.        ,
          0.14265751, -0.        ,  0.        ,  0.02593517,  0.       

#### Explanation with MatrixProfile Window segmentation- slopes-sorted

In [ ]:
#LimeTS object for matrix profile segmentation= slopes-sorted
tic = timeit.default_timer()
#segment object, MatrixProfileSegmentation object has slopes, bins-min, bins-max segmentation techniques
seg_slopes=MatrixProfileSegmentation(partitions=4, win_length=20)

lime_slopes=LimeTS(kernel=lasso_classifier, segmenter=seg_slopes, sampler=per)
lime_values_slopes=[lime_slopes.explain(sample[i], predict_fn,
                                                  segmentation_method='slopes-sorted') for i in
                    range(len(sample))]

print('Total time: ' + str(timeit.default_timer()-tic))

In [ ]:
with open("Beijing_air_quality_rnn_lime_values_slopes.dill", 'wb') as f:
    dill.dump(lime_values_slopes, f)

#### Explanation with SAX Transformation

In [ ]:
#LimeTS object for SAX segmentation
tic = timeit.default_timer()
#create segment object for SAX Transformation
seg_sax=SAXSegmentation(partitions=4, win_length=10)

lime_sax=LimeTS(kernel=lasso_classifier, segmenter=seg_sax, sampler=per, n_samples=24)
lime_values_sax=[lime_sax.explain(sample[i], predict_fn) for i in range(len(sample))]

print('Total time: ' + str(timeit.default_timer()-tic))

In [ ]:
with open("Beijing_air_quality_rnn_lime_values_sax.dill", 'wb') as f:
    dill.dump(lime_values_sax, f)